# Hyperparameter tuning

Machine learning models always have a set of parameters that can be set. Some examples are the maximum depth of a tree in a tree-based model, or the amount of trees to use. These are called hyperparameters, and the optimal combination depends on each individual problem.

Tuning these parameters can be done in different ways. Usually, a dictionary is set up containing the different possibilities to try out.

In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error
import lightgbm as lgb

In [2]:
df = pd.read_csv('data/chl_regression_tutorial.csv')
df_train, df_test = train_test_split(df, test_size=0.2, random_state=42)

features = ['rho_443_a', 'rho_492_a', 'rho_560_a', 'rho_665_a', 'rho_704_a', 'rho_740_a', 'rho_783_a', 'rho_865_a']
target = 'CHL'

X_train = df_train[features]
y_train = df_train[target]

X_test = df_test[features]
y_test = df_test[target]

## Grid search
One way to find the optimal parameters is the "brute-force" method, by trying out each individual combination. This is called grid-search, where you define a "hyperparameter grid", and evaluate the performance of each combination using cross-validation.

In [3]:
from sklearn.model_selection import GridSearchCV

model = lgb.LGBMRegressor()

hyperparameter_search_space = {
    'n_estimators': [10, 100, 1000],
    'learning_rate': [0.01, 0.1, 1],
    'max_depth': [3, 5, 7],
}

search = GridSearchCV(model, hyperparameter_search_space, n_jobs=-1, cv=5, scoring='neg_mean_squared_error', verbose=1)
search.fit(X_train, y_train)

print('Best hyperparameters:', search.best_params_)

Fitting 5 folds for each of 27 candidates, totalling 135 fits
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000358 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -in

We can then train the model using the found parameters and evaluate.

In [4]:
model = lgb.LGBMRegressor(**search.best_params_)
model.fit(X_train, y_train)

y_pred = model.predict(X_test)
print('Test MSE:', mean_squared_error(y_test, y_pred))

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000357 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

## Random search

When your search space is large, an exhaustive search as is done in grid search can be unfeasible. In many cases, random search also does a good job, where random combinations from your set are tried out, and you retain the combination with the best results.

In [5]:
from sklearn.model_selection import RandomizedSearchCV
from scipy.stats import randint as sp_randint

model = lgb.LGBMRegressor()

hyperparameter_search_space = {
    'n_estimators': sp_randint(10, 1000),
    'learning_rate': [0.01, 0.1, 1],
    'max_depth': sp_randint(3, 10),
}

search = RandomizedSearchCV(model, hyperparameter_search_space, n_iter=10, n_jobs=-1, cv=5, scoring='neg_mean_squared_error', verbose=1)
search.fit(X_train, y_train)
print('Best hyperparameters:', search.best_params_)

model = lgb.LGBMRegressor(**search.best_params_)
model.fit(X_train, y_train)

y_pred = model.predict(X_test)
print('Test MSE:', mean_squared_error(y_test, y_pred))

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001001 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf

## Optuna library

There are also python packages such as Optuna that implemeny more complex hyperparameter tuning strategies. Instead of doing a random search, Optuna's algorithm tries to identify the most promising area's of the search space based on prior evaluations.

In [6]:
# using Optuna
import optuna

optuna.logging.set_verbosity(optuna.logging.INFO)

def objective(trial):
    n_estimators = trial.suggest_int('n_estimators', 10, 1000)
    learning_rate = trial.suggest_float('learning_rate', 1e-3, 1, log=True)
    max_depth = trial.suggest_int('max_depth', 3, 10)

    model = lgb.LGBMRegressor(n_estimators=n_estimators, learning_rate=learning_rate, max_depth=max_depth)
    model.fit(X_train, y_train)

    y_pred = model.predict(X_test)
    return mean_squared_error(y_test, y_pred)

sampler = optuna.samplers.TPESampler(seed=42)
study = optuna.create_study(direction='minimize', sampler=sampler)
study.optimize(objective, n_trials=100)

print('Best hyperparameters:', study.best_params)

model = lgb.LGBMRegressor(**study.best_params)
model.fit(X_train, y_train)

y_pred = model.predict(X_test)
print('Test MSE:', mean_squared_error(y_test, y_pred))

c:\Users\jmassant\AppData\Local\anaconda3\envs\machine_learning_tutorial\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2024-11-27 13:53:48,553] A new study created in memory with name: no-name-af9a1a5a-b2df-48ca-a7d8-16f9c99e3fdf


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000219 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2024-11-27 13:53:48,849] Trial 0 finished with value: 3.9582895354072942 and parameters: {'n_estimators': 381, 'learning_rate': 0.711447600934342, 'max_depth': 8}. Best is trial 0 with value: 3.9582895354072942.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-11-27 13:53:49,225] Trial 1 finished with value: 6.276020288307635 and parameters: {'n_estimators': 603, 'learning_rate': 0.0029380279387035343, 'max_depth': 4}. Best is trial 0 with value: 3.9582895354072942.
[I 2024-11-27 13:53:49,305] Trial 2 finished with value: 3.5012417575314347 and parameters: {'n_estimators': 67, 'learning_rate': 0.39676050770529875, 'max_depth': 7}. Best is trial 2 with value: 3.5012417575314347.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-11-27 13:54:34,159] Trial 98 finished with value: 2.9868126003429065 and parameters: {'n_estimators': 819, 'learning_rate': 0.13254473759134605, 'max_depth': 5}. Best is trial 83 with value: 2.7783331409279315.


[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000361 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2024-11-27 13:54:34,418] Trial 99 finished with value: 2.857310300555626 and parameters: {'n_estimators': 490, 'learning_rate': 0.10201979888090675, 'max_depth': 4}. Best is trial 83 with value: 2.7783331409279315.


Best hyperparameters: {'n_estimators': 773, 'learning_rate': 0.14482642335895063, 'max_depth': 4}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000420 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2040
[LightGBM] [Info] Number of data points in the train set: 8000, number of used features: 8
[LightGBM] [Info] Start training from score 4.527730
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further split